<a href="https://colab.research.google.com/github/virbickt/default-risk-prediction/blob/main/feature_engineering_02.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Other sources

In what follows we will be using a particular way of merging tables in order to avoid memory crashes due to duplicated indices. All credit for showing me the way to circumvent this problem goes to [ovidijusku](https://github.com/ovidijusku).

## Installments

Since we are interested in those applicants who might have problems paying back their loan, it seems natural to assume that those will eventually default who had already been late with the payments in the past. For this reason, let us make two new features `DIFF_IN_AMOUNT_PAID` to track the payments that we short and `DIFF_IN_DAYS` to track the difference in days for when was that the payment was supposed to be made and when it was actually made.

In [ ]:
inst_df['DIFF_IN_AMOUNT_PAID'] = inst_df['AMT_INSTALMENT'] - inst_df['AMT_PAYMENT']
inst_df['DIFF_IN_DAYS'] = inst_df['DAYS_INSTALMENT'] - inst_df['DAYS_ENTRY_PAYMENT']

### Number of time applicant was late

In [ ]:
inst_df.head()

SK_ID_PREV  SK_ID_CURR  ...  DIFF_IN_AMOUNT_PAID  DIFF_IN_DAYS
0     1054186      161674  ...                0.000           7.0
1     1330831      151639  ...                0.000           0.0
2     2085231      193053  ...                0.000           0.0
3     2452527      199697  ...                0.000           8.0
4     2714724      167756  ...                4.455         -17.0

[5 rows x 10 columns]

Moreover, if the applicant has been made late for at least a day for that particular loan, we flag that it as an instance of being late to pay the loan time.

In [ ]:
inst_df['LATE_DAYS'] = 0
inst_df.loc[inst_df['DIFF_IN_DAYS'] > 0, 'LATE_DAYS'] = 1

In [ ]:
late_counts_df = (
    inst_df.groupby(["SK_ID_PREV", "LATE_DAYS"]).count().reset_index().iloc[:, :3]
)
inst_pivot_df = late_counts_df.pivot_table(
    "SK_ID_CURR", "SK_ID_PREV", "LATE_DAYS"
).fillna(0)
inst_pivot_df.columns = ["ON_TIME", "LATE"]
inst_pivot_df

ON_TIME  LATE
SK_ID_PREV               
1000001         0.0   2.0
1000002         0.0   4.0
1000003         0.0   3.0
1000004         0.0   7.0
1000005         2.0   9.0
...             ...   ...
2843495         2.0   5.0
2843496        21.0  13.0
2843497         7.0  13.0
2843498         1.0   5.0
2843499         0.0  10.0

[997752 rows x 2 columns]

We make an additional feature `LATE_ON_TIME_DAYS_RATIO` so to track the ratio of the number of times the applicant was late to the number of times the applicant was on time.

In [ ]:
inst_pivot_df['LATE_ON_TIME_DAYS_RATIO'] = inst_pivot_df['LATE'] / (inst_pivot_df['LATE'] + inst_pivot_df['ON_TIME'])
inst_pivot_df

ON_TIME  LATE  LATE_ON_TIME_DAYS_RATIO
SK_ID_PREV                                        
1000001         0.0   2.0                 1.000000
1000002         0.0   4.0                 1.000000
1000003         0.0   3.0                 1.000000
1000004         0.0   7.0                 1.000000
1000005         2.0   9.0                 0.818182
...             ...   ...                      ...
2843495         2.0   5.0                 0.714286
2843496        21.0  13.0                 0.382353
2843497         7.0  13.0                 0.650000
2843498         1.0   5.0                 0.833333
2843499         0.0  10.0                 1.000000

[997752 rows x 3 columns]

In what follows we will be repeatedly using an empty data frame that so that the information from the table (`installments` in this case) can be carried over to `application_train` (credit goes to ovidijusku). Without being aware of this technique, we have been running into problems with running out of RAM as there duplicates in the column that would be used for merging tables.

In [ ]:
export_df = pd.DataFrame()
export_df["SK_ID_PREV"] = inst_df.SK_ID_PREV.unique()

In [ ]:
export_df = pd.merge(
    export_df, inst_pivot_df, left_on="SK_ID_PREV", right_on="SK_ID_PREV", how="left"
)
export_df

SK_ID_PREV  ON_TIME  LATE  LATE_ON_TIME_DAYS_RATIO
0          1054186      0.0  12.0                 1.000000
1          1330831     86.0  17.0                 0.165049
2          2085231      2.0   1.0                 0.333333
3          2452527      0.0   6.0                 1.000000
4          2714724      2.0   4.0                 0.666667
...            ...      ...   ...                      ...
997747     2363009      0.0   1.0                 1.000000
997748     1231783      0.0   1.0                 1.000000
997749     1984920      0.0   1.0                 1.000000
997750     1946334      0.0   1.0                 1.000000
997751     1276288      0.0   1.0                 1.000000

[997752 rows x 4 columns]

### Times applicant was short in payment

We flag the occurances when the applicant was short on payment in the similar manner:

In [ ]:
inst_df['SHORT'] = 0
inst_df.loc[inst_df['DIFF_IN_AMOUNT_PAID'] > 0, 'SHORT'] = 1

In [ ]:
late_counts_df = (
    inst_df.groupby(["SK_ID_PREV", "SHORT"]).count().reset_index().iloc[:, :3]
)
inst_pivot_df = late_counts_df.pivot_table("SK_ID_CURR", "SK_ID_PREV", "SHORT").fillna(
    0
)
inst_pivot_df.columns = ["FULL", "SHORT"]

In [ ]:
inst_pivot_df

FULL  SHORT
SK_ID_PREV             
1000001      2.0    0.0
1000002      4.0    0.0
1000003      3.0    0.0
1000004      7.0    0.0
1000005      9.0    2.0
...          ...    ...
2843495      7.0    0.0
2843496     30.0    4.0
2843497     20.0    0.0
2843498      6.0    0.0
2843499     10.0    0.0

[997752 rows x 2 columns]

We also track the ratio of the number of times the applicant was short in his payment to the number of times when he paid the installment in full:

In [ ]:
inst_pivot_df["SHORT_ON_PAYMENT_RATIO"] = inst_pivot_df["SHORT"] / (
    inst_pivot_df["SHORT"] + inst_pivot_df["FULL"]
)
inst_pivot_df

FULL  SHORT  SHORT_ON_PAYMENT_RATIO
SK_ID_PREV                                     
1000001      2.0    0.0                0.000000
1000002      4.0    0.0                0.000000
1000003      3.0    0.0                0.000000
1000004      7.0    0.0                0.000000
1000005      9.0    2.0                0.181818
...          ...    ...                     ...
2843495      7.0    0.0                0.000000
2843496     30.0    4.0                0.117647
2843497     20.0    0.0                0.000000
2843498      6.0    0.0                0.000000
2843499     10.0    0.0                0.000000

[997752 rows x 3 columns]

In [ ]:
export_df = pd.merge(
    export_df, inst_pivot_df, left_on="SK_ID_PREV", right_on="SK_ID_PREV", how="left"
)

## Credit card balance

More financial burden, more risk of defaulting on the loan. Another way to see whether the applicant is already burdened by other financial commitments is to look whether he has any other loans that are still active:

In [ ]:
# select all the numerical variables in credit.csv (excluding SK_ID_PREV and SK_ID_CURR)
cred_cats = cred_card_df.select_dtypes(exclude="object").columns.tolist()[2:] 

# extracting averages
averages_df = cred_card_df.groupby(["SK_ID_PREV"])[cred_cats].mean()

averages_df

MONTHS_BALANCE   AMT_BALANCE  ...     SK_DPD  SK_DPD_DEF
SK_ID_PREV                                ...                       
1000018               -4.0  74946.285000  ...   0.000000    0.000000
1000030               -4.5  55991.064375  ...   0.000000    0.000000
1000031               -8.5  52394.439375  ...   0.000000    0.000000
1000035               -4.0      0.000000  ...   0.000000    0.000000
1000077               -7.0      0.000000  ...   0.000000    0.000000
...                    ...           ...  ...        ...         ...
2843476              -49.0  37937.812263  ...  15.031579    3.473684
2843477              -43.0   1663.076647  ...   0.000000    0.000000
2843478              -46.5   5111.405000  ...   0.000000    0.000000
2843493               -8.0  59139.927000  ...   0.000000    0.000000
2843496               -8.0  44373.681000  ...   0.000000    0.000000

[104307 rows x 20 columns]

In [ ]:
export_df = pd.merge(
    export_df,
    averages_df,
    left_on="SK_ID_PREV",
    right_on="SK_ID_PREV",
    how="left",
)

In [ ]:
# extracting status counts
status_counts_df = (
    cred_card_df.groupby(["SK_ID_PREV", "NAME_CONTRACT_STATUS"])
    .count()
    .reset_index()
)

# making pivot table of status counts
status_pivot_df = status_counts_df.pivot_table(
    "MONTHS_BALANCE", "SK_ID_PREV", "NAME_CONTRACT_STATUS"
).fillna(0)

status_pivot_df

NAME_CONTRACT_STATUS  Active  Approved  ...  Sent proposal  Signed
SK_ID_PREV                              ...                       
1000018                  5.0       0.0  ...            0.0     0.0
1000030                  8.0       0.0  ...            0.0     0.0
1000031                 16.0       0.0  ...            0.0     0.0
1000035                  5.0       0.0  ...            0.0     0.0
1000077                 11.0       0.0  ...            0.0     0.0
...                      ...       ...  ...            ...     ...
2843476                 95.0       0.0  ...            0.0     0.0
2843477                 85.0       0.0  ...            0.0     0.0
2843478                 90.0       0.0  ...            0.0     0.0
2843493                 15.0       0.0  ...            0.0     0.0
2843496                 15.0       0.0  ...            0.0     0.0

[104307 rows x 7 columns]

In [ ]:
# assigning pivot table to export df
export_df = pd.merge(
    export_df,
    status_pivot_df,
    left_on="SK_ID_PREV",
    right_on="SK_ID_PREV",
    how="left",
)

## Previous application

In [ ]:
# merging export_df with previous_application_df and filling the missing values
prev_app = pd.merge(
    prev_app,
    export_df,
    left_on="SK_ID_PREV",
    right_on="SK_ID_PREV",
    how="left",
).fillna(0)

In [ ]:
prev_app

SK_ID_PREV  SK_ID_CURR  ... Sent proposal  Signed
0           2030495      271877  ...           0.0     0.0
1           2802425      108129  ...           0.0     0.0
2           2523466      122040  ...           0.0     0.0
3           2819243      176158  ...           0.0     0.0
4           1784265      202054  ...           0.0     0.0
...             ...         ...  ...           ...     ...
1670209     2300464      352015  ...           0.0     0.0
1670210     2357031      334635  ...           0.0     0.0
1670211     2659632      249544  ...           0.0     0.0
1670212     2785582      400317  ...           0.0     0.0
1670213     2418762      261212  ...           0.0     0.0

[1670214 rows x 70 columns]

In [ ]:
# extracting average list
avg_list = prev_app.select_dtypes(exclude="object").iloc[:, 2:].columns

# extracting averages
averages_df = prev_app.groupby(["SK_ID_CURR"])[avg_list].mean()

In [ ]:
prev_app = pd.merge(prev_app, 
                    averages_df,
                    left_on="SK_ID_CURR",
                    right_on="SK_ID_CURR",
                    how="left",
)

In [ ]:
# extracting counts
counts_df = (
    prev_app.groupby("SK_ID_CURR").count().reset_index().iloc[:, :2]
)
counts_df.columns = ["SK_ID_CURR", "PREV_COUNTS"]
counts_df

SK_ID_CURR  PREV_COUNTS
0           100001            1
1           100002            1
2           100003            3
3           100004            1
4           100005            2
...            ...          ...
338852      456251            1
338853      456252            1
338854      456253            2
338855      456254            2
338856      456255            8

[338857 rows x 2 columns]

In [ ]:
# assigning counts to export df
prev_app = pd.merge(
    prev_app,
    counts_df,
    left_on="SK_ID_CURR",
    right_on="SK_ID_CURR",
    how="left",
)

# filling missing values
prev_app = prev_app.fillna(0)

In [ ]:
prev_app.to_csv("/content/drive/MyDrive/341/prev_READY.csv")

## Bureau and bureau balance

In [ ]:
bureau_balance.groupby(["SK_ID_BUREAU", "STATUS"]).count()
# creating new dataframe which could be afterwards merged with bureau

new_extracted_df = bureau_balance.groupby(["SK_ID_BUREAU"]).count().reset_index()

new_extracted_df = new_extracted_df.drop(["MONTHS_BALANCE"], axis=1)

new_extracted_df.columns = ["SK_ID_BUREAU", "COUNT"]

new_extracted_df

SK_ID_BUREAU  COUNT
0            5001709     97
1            5001710     83
2            5001711      4
3            5001712     19
4            5001713     22
...              ...    ...
817390       6842884     48
817391       6842885     24
817392       6842886     33
817393       6842887     37
817394       6842888     62

[817395 rows x 2 columns]

In [ ]:
# extracting status counts
status_counts_df = (
    bureau_balance.groupby(["SK_ID_BUREAU", "STATUS"]).count().reset_index()
)

status_pivot_df = status_counts_df.pivot_table(
    "MONTHS_BALANCE", "SK_ID_BUREAU", "STATUS"
)

# filling NaN values with 0
status_pivot_df = status_pivot_df.fillna(0)

In [ ]:
# merging two dataframes
new_extracted_df = pd.merge(
    new_extracted_df, status_pivot_df, left_on="SK_ID_BUREAU", right_on="SK_ID_BUREAU"
)

# merging bureau_balance main insights to bureau
bureau = pd.merge(bureau, new_extracted_df, on="SK_ID_BUREAU", how="left")

In [ ]:
# creating df for exporting to train_df and test_df
new_export_df = pd.DataFrame()
new_export_df["SK_ID_CURR"] = bureau.SK_ID_CURR.unique()

# extracting status counts
status_counts_df = bureau.groupby(["SK_ID_CURR", "CREDIT_ACTIVE"]).count().reset_index()


# making pivot table of status counts
status_pivot_df = status_counts_df.pivot_table(
    "CREDIT_CURRENCY", "SK_ID_CURR", "CREDIT_ACTIVE"
)
# filling NaN values with 0
status_pivot_df = status_pivot_df.fillna(0)

status_pivot_df

CREDIT_ACTIVE  Active  Bad debt  Closed  Sold
SK_ID_CURR                                   
100001            3.0       0.0     4.0   0.0
100002            2.0       0.0     6.0   0.0
100003            1.0       0.0     3.0   0.0
100004            0.0       0.0     2.0   0.0
100005            2.0       0.0     1.0   0.0
...               ...       ...     ...   ...
456249            2.0       0.0    11.0   0.0
456250            2.0       0.0     1.0   0.0
456253            2.0       0.0     2.0   0.0
456254            0.0       0.0     1.0   0.0
456255            5.0       0.0     6.0   0.0

[305811 rows x 4 columns]

In [ ]:
import plotly.graph_objects as go

fig = go.Figure()
fig.add_trace(go.Histogram(name="Number of active credits", x=status_pivot_df.Active))
fig.add_trace(
    go.Histogram(
        name="Number of credits marked as 'Bad debt'", x=status_pivot_df["Bad debt"]
    )
)
fig.add_trace(go.Histogram(name="Number of closed credits", x=status_pivot_df.Closed))
fig.add_trace(go.Histogram(name="Number of sold credits", x=status_pivot_df.Sold))

# Overlaying histograms for train and test sets
fig.update_layout(
    barmode="overlay",
    title="Counts of the instances credits in one of the four observed status",
    xaxis_title="Counts of instances",
    yaxis_title="Count of applicants",
    title_font_family="Raleway",
    xaxis=dict(tickmode="linear", tick0=10, dtick=10),
)
fig.update_xaxes(title_font_family="Raleway")

# Reducing opacity
fig.update_traces(opacity=0.75)
fig.show()

In [ ]:
# merging pivot table with new_export_df
new_export_df = pd.merge(
    new_export_df,
    status_pivot_df,
    left_on="SK_ID_CURR",
    right_on="SK_ID_CURR",
    how="left",
)

# extracting currency counts
currency_counts_df = (
    bureau.groupby(["SK_ID_CURR", "CREDIT_CURRENCY"]).count().reset_index()
)

# making pivot table of status counts
currency_pivot_df = currency_counts_df.pivot_table(
    "CREDIT_ACTIVE", "SK_ID_CURR", "CREDIT_CURRENCY"
)
# filling NaN values with 0
currency_pivot_df = currency_pivot_df.fillna(0)

currency_pivot_df

CREDIT_CURRENCY  currency 1  currency 2  currency 3  currency 4
SK_ID_CURR                                                     
100001                  7.0         0.0         0.0         0.0
100002                  8.0         0.0         0.0         0.0
100003                  4.0         0.0         0.0         0.0
100004                  2.0         0.0         0.0         0.0
100005                  3.0         0.0         0.0         0.0
...                     ...         ...         ...         ...
456249                 13.0         0.0         0.0         0.0
456250                  3.0         0.0         0.0         0.0
456253                  4.0         0.0         0.0         0.0
456254                  1.0         0.0         0.0         0.0
456255                 11.0         0.0         0.0         0.0

[305811 rows x 4 columns]

In [ ]:
# merging pivot table with new_export_df
new_export_df = pd.merge(
    new_export_df,
    currency_pivot_df,
    left_on="SK_ID_CURR",
    right_on="SK_ID_CURR",
    how="left",
)

In [ ]:
avg_list = [
    "DAYS_CREDIT",
    "CREDIT_DAY_OVERDUE",
    "DAYS_CREDIT_ENDDATE",
    "DAYS_ENDDATE_FACT",
    "AMT_CREDIT_MAX_OVERDUE",
    "CNT_CREDIT_PROLONG",
    "AMT_CREDIT_SUM",
    "AMT_CREDIT_SUM_DEBT",
    "AMT_CREDIT_SUM_LIMIT",
    "AMT_CREDIT_SUM_OVERDUE",
    "DAYS_CREDIT_UPDATE",
    "AMT_ANNUITY"
]

# extracting averages
averages_df = bureau.groupby(["SK_ID_CURR"])[avg_list].mean()

# putting feature into new_export_df
new_export_df = pd.merge(
    new_export_df,
    averages_df,
    left_on="SK_ID_CURR",
    right_on="SK_ID_CURR",
    how="left",
)

In [ ]:
# merging with train_df and test_df
UPDATED_train = pd.merge(
    UPDATED_train,
    new_export_df,
    left_on="SK_ID_CURR",
    right_on="SK_ID_CURR",
    how="left",
)

UPDATED_test = pd.merge(
    UPDATED_test,
    new_export_df,
    left_on="SK_ID_CURR",
    right_on="SK_ID_CURR",
    how="left",
)

UPDATED_train.to_csv("/content/drive/MyDrive/341/UPDATED_full_train.csv")
UPDATED_test.to_csv("/content/drive/MyDrive/341/UPDATED_full_test.csv")